In [101]:
import pandas as pd
import numpy as np 
import glob
import os 
from openpyxl import load_workbook
from openpyxl.styles import PatternFill, Font
from datetime import datetime

In [102]:
hoje = datetime.today().strftime('%Y-%m-%d')

In [103]:
# O QUE PRECISA PRA RODAR ESSE CÓDIGO:

# Arquivo Draft
# Arquivo Estoque
# Arquivo BI preço
# Arquivo pdv
# Arquivo Calendario
# Arquivo tabela de compra

#Atualizar o nome da marca no filtro do estoque.

In [104]:
df_tabela = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\BOTICARIO\C11\TABELA DE PEDIDOS\Pedidos Semanais Especiais - BOT - 202511 (1).xlsx")

df_tabela = df_tabela[df_tabela['Ação revendedor'].notna() | df_tabela['Ação consumidor'].notna()]

df_tabela = df_tabela[df_tabela['Região'] == 'NNE'] 

df_tabela = df_tabela[(df_tabela['Canal'] != 'Ecomm')]

#df_tabela['Canal'] = np.where((df_tabela['Canal'] == "Loja") | (df_tabela['Canal'] == "Todos") | (df_tabela['Canal'] == "Loja | VD"),"TODOS","VD")

df_tabela = df_tabela[(df_tabela['Categoria'] != "EMBALAGENS") | (df_tabela['Categoria'] != "SUPORTE À VENDA")]

df_tabela = df_tabela[df_tabela['Tipo de pedido'] == 'Semanal']

df_tabela = df_tabela[~df_tabela['Descrição'].str.contains('PRM')]

df_tabela = df_tabela[df_tabela['Tipo de produto']!= 'EDICAO LIMITADA']

df_tabela['Ação revendedor'] = np.where(df_tabela['Ação revendedor'].isna(),df_tabela['Ação consumidor'],df_tabela['Ação revendedor'])

df_tabela['Percentual de desconto revendedor'] = np.where(df_tabela['Percentual de desconto revendedor'].isna(),df_tabela['Percentual de desconto consumidor'],df_tabela['Percentual de desconto revendedor'])

df_tabela['MATCH'] = 1



In [105]:
df_tabela['Código'].shape

(332,)

In [106]:
df_tabela.shape

(332, 24)

In [107]:
df_pdv = pd.read_excel(r"C:\Users\joao.herculano\Documents\PDV_ATT.xlsx")

df_pdv_origi = pd.read_excel(r"C:\Users\joao.herculano\Documents\PDV_ATT.xlsx")

df_pdv = df_pdv.rename(columns={'DESCRIÇÃO':'DESCRIÇÃO PDV'})

df_pdv = df_pdv[df_pdv['GESTÃO']!="Inativa"]

df_pdv = df_pdv.drop(columns=['REGIÃO', 'ESTADO','CIDADE','GESTÃO', 'STATUS'])

df_pdv['PDV'] = df_pdv['PDV DESC'].str.split("-").str[0].str.strip()

df_pdv = df_pdv[df_pdv['CANAL']!='MTZ']

#df_pdv['CANAL'] = np.where((df_pdv['CANAL']=='LJ')|(df_pdv['CANAL']=='HIB')|(df_pdv['CANAL']=='CD'),'TODOS','VD')

df_pdv['MATCH'] = 1



In [108]:
df_pdv = df_pdv.drop(columns=['pdv como texto','PDV DESC'])

In [109]:
# Caminho onde estão as subpastas com os arquivos CSV

# Set the path to the folder containing CSV files
folder_path = r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\BOTICARIO\C11\DRAFT_PDVS_SEM_"  # arquivo dos drafts

# Pattern to match all CSV files
csv_files = glob.glob(os.path.join(folder_path, '*.csv'))

# Read and concat all CSVs
df_draft = pd.concat([pd.read_csv(file) for file in csv_files], ignore_index=True)

df_draft.shape


C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_17756\3645011820.py:10: DtypeWarning: Columns (6,7) have mixed types. Specify dtype option on import or set low_memory=False.
  df_draft = pd.concat([pd.read_csv(file) for file in csv_files], ignore_index=True)


(127198, 46)

In [110]:
df_draft = df_draft.drop(columns=['Descrição','Compra inteligente semanal/Sugestão de compra',
       'Compra inteligente Próximo Ciclo',
       'Compra inteligente Próximo Ciclo + 1','Planograma', 'Quantidade por caixa', 'Preço Sell In', 'Quantidade',
       'Item analisado', 'Subcategoria',
       'Lançamento', 'Desativação',
       'Promoção Próximo Ciclo', 'Categoria'])

In [111]:


# Caminho onde estão as subpastas com os arquivos CSV
pasta_entrada =  r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\BOTICARIO\C11\estoque"

# Lista todas as subpastas dentro de "ESTOQUE"
subpastas = [os.path.join(pasta_entrada, d) for d in os.listdir(pasta_entrada) if os.path.isdir(os.path.join(pasta_entrada, d))]

df_list = []

# Percorre todas as subpastas
for subpasta in subpastas:
    arquivos = [f for f in os.listdir(subpasta) if f.endswith(".csv")]
    nome_pasta = os.path.basename(subpasta)  # Obtém o nome da pasta

    for arquivo in arquivos:
        caminho_arquivo = os.path.join(subpasta, arquivo)
        try:
            df = pd.read_csv(caminho_arquivo, encoding="utf-8", low_memory=False)  # Melhor para grandes volumes de dados
            df["Arquivo_Origem"] = arquivo  # Adiciona o nome do arquivo de origem
            df["Pasta_Origem"] = nome_pasta  # Adiciona o nome da pasta de origem
            df_list.append(df)
        except Exception as e:
            print(f"Erro ao ler o arquivo {arquivo}: {e}")

if df_list:
    df_estoque = pd.concat(df_list, ignore_index=True)

df_estoque['PDV'] = df_estoque['PDV'].astype(str)

df_estoque['SKU_FINAL'] = np.where(df_estoque['SKU_PARA'] == "-", df_estoque['SKU'], df_estoque['SKU_PARA'])

df_estoque['SKU_FINAL']=df_estoque['SKU_FINAL'].astype(str)


In [112]:
df_tabela.columns

Index(['Ciclo', 'Região', 'Canal', 'Código', 'Descrição', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Subcategoria', 'Quantidade por caixa', 'Tipo de promoção', 'Catálogo',
       'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'Sortimento P', 'Sortimento M',
       'Sortimento G', 'MATCH'],
      dtype='object')

In [113]:
df_tabela.shape

(332, 24)

In [114]:
df_tabela['Canal'].value_counts()

Canal
Todos           183
Loja             72
VD               67
Loja | VD         6
Ecomm | VD        2
Ecomm | Loja      2
Name: count, dtype: int64

In [14]:
df_estoque['SKU_FINAL'] = df_estoque['SKU_FINAL'].astype('Int64')

In [15]:
df_tabela = pd.merge(left=df_tabela,right=df_estoque[['SKU','SKU_FINAL']],left_on='Código',right_on='SKU',how='left')

df_tabela['Código'] = df_tabela['SKU_FINAL']

df_tabela = df_tabela.drop(columns=['SKU','SKU_FINAL'])

In [16]:
df_tabela['Código'].nunique()

315

In [17]:
df_tabela = pd.merge(left=df_tabela,right=df_estoque[['SKU','SKU_FINAL']],left_on='Código',right_on='SKU_FINAL',how='left')

df_tabela['Código'] = df_tabela['SKU_FINAL']

df_tabela = df_tabela.drop(columns=['SKU','SKU_FINAL'])



In [18]:
df_tabela = df_tabela.drop_duplicates()

In [19]:
df_tabela.to_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\BOTICARIO\C11\teste.xlsx",index=False)

In [20]:
df_tabela

Ciclo Região         Canal  Código  \
0        202511    NNE            VD   74438   
7440     202511    NNE            VD   57210   
12624    202511    NNE            VD   57211   
17953    202511    NNE            VD   57209   
23578    202511    NNE            VD   57208   
...         ...    ...           ...     ...   
1918086  202511    NNE          Loja   55477   
1918662  202511    NNE    Ecomm | VD   83961   
1926362  202511    NNE    Ecomm | VD   73614   
1931987  202511    NNE  Ecomm | Loja   52948   
1937171  202511    NNE  Ecomm | Loja   58987   

                                        Descrição  IAF Tipo de pedido Foco  \
0                           ARBO DES COL 100ml V4  Não        Semanal  Não   
7440       AU MIGOS PETS BANHO SECO ADULTOS 240ml  Não        Semanal  Não   
12624              AU MIGOS PETS COL ADULTOS 60ml  Não        Semanal  Não   
17953             AU MIGOS PETS COL FILHOTES 60ml  Não        Semanal  Não   
23578            AU MIGOS PETS COND ADULTOS 400ml  Não        Semanal  Não   
...                                           ...  ...            ...  ...   
1918086  SCH BOTIK SERUM FAC RESV/SILICIO VDA 2ml  Não        Semanal  Não   
1918662                 ARBO DES BDY SPR 100ml V6  Não        Semanal  Não   
1926362              COFFEE DES COL DUO MAN 100ml  Não        Semanal  Não   
1931987          NSPA CREM ESF CPO AMEI DOUR 200g  Não        Semanal  Não   
1937171    NSPA OL BIF DES HID CPO UVA MERL 200ml  Não        Semanal  Não   

        Unidade de negócio          Marca  ... Catálogo Tipo de produto  \
0                      BOT           ARBO  ...      Sim         REGULAR   
7440                   BOT  AU.MIGOS PETS  ...      Sim         REGULAR   
12624                  BOT  AU.MIGOS PETS  ...      Sim         REGULAR   
17953                  BOT  AU.MIGOS PETS  ...      Sim         REGULAR   
23578                  BOT  AU.MIGOS PETS  ...      Sim         REGULAR   
...                    ...            ...  ...      ...             ...   
1918086                BOT          BOTIK  ...      Sim         REGULAR   
1918662                BOT           ARBO  ...      Sim         REGULAR   
1926362                BOT         COFFEE  ...      Sim         REGULAR   
1931987                BOT     NATIVA SPA  ...      Sim         REGULAR   
1937171                BOT     NATIVA SPA  ...      Sim         REGULAR   

                                           Ação consumidor  \
0                                                      NaN   
7440                                                   NaN   
12624                                                  NaN   
17953                                                  NaN   
23578                                                  NaN   
...                                                    ...   
1918086  [BOT] AÇÃO DE FLUXO BOTIK CICACERAMIDAS COM DE...   
1918662               [ECOMM] PAIS 2025 - COMBO ARBO - NNE   
1926362          [ECOMM] PAIS 2025 - COMBO COFFEE E BOTMEN   
1931987  [LOJA/ECOMM] ITENS SELECIONADOS DE NATIVA SPA ...   
1937171  [LOJA/ECOMM] ITENS SELECIONADOS DE NATIVA SPA ...   

        Percentual de desconto consumidor  \
0                                    0,00   
7440                                 0,00   
12624                                0,00   
17953                                0,00   
23578                                0,00   
...                                   ...   
1918086                             10,00   
1918662                             21,49   
1926362                             18,67   
1931987                              7,82   
1937171                             14,88   

                                           Ação revendedor  \
0                   VD - FAVORITOS PARA INÍCIOS ARBO - C11   
7440     VD - LUCRATIVIDADE BASE AUMIGOS - BRONZE | VD ...   
12624    VD - LUCRATIVIDADE BASE AUMIGOS - BRONZE | VD ...   
17953    VD - LUCRATIVIDADE BASE AUMIGOS - BRONZE | VD ...   

In [21]:
df_estoque = df_estoque.drop(columns=['DESCRICAO', 'CATEGORIA', 'CLASSE', 'FASES PRODUTO',
       'LANCAMENTO', 'DESATIVACAO','COBERTURA ALVO',
       'ESTOQUE DE SEGURANCA','COBERTURA PROJETADA', 
       'Pasta_Origem'])

In [22]:
df_estoque

SKU SKU_PARA     PDV  ESTOQUE ATUAL  ESTOQUE EM TRANSITO  \
0       94394        -   20968            0.0                  0.0   
1       94394        -   20969            0.0                  0.0   
2       94394        -   20970            0.0                  0.0   
3       94394        -   20986            0.0                  0.0   
4       94394        -   20988            0.0                  0.0   
...       ...      ...     ...            ...                  ...   
454599   4438        -  910291            9.0                 10.0   
454600   4431        -   21007            0.0                  0.0   
454601   4431        -  910173            2.0                 10.0   
454602   4431        -  910291            1.0                 10.0   
454603   1594        -   21007            2.0                  0.0   

        PEDIDO PENDENTE  DDV PREVISTO  COBERTURA ATUAL  \
0                   0.0           NaN              NaN   
1                   0.0           NaN              NaN   
2                   0.0           NaN              NaN   
3                   0.0           NaN              NaN   
4                   0.0           NaN              NaN   
...                 ...           ...              ...   
454599              0.0          0.78             11.0   
454600              0.0           NaN              NaN   
454601              0.0          0.40              5.0   
454602              0.0          0.78              1.0   
454603              0.0           NaN              NaN   

        COBERTURA ATUAL + TRANSITO Arquivo_Origem  SKU_FINAL  
0                              NaN        BOT.csv      94394  
1                              NaN        BOT.csv      94394  
2                              NaN        BOT.csv      94394  
3                              NaN        BOT.csv      94394  
4                              NaN        BOT.csv      94394  
...                            ...            ...        ...  
454599                        24.0        QDB.csv       4438  
454600                         NaN        QDB.csv       4431  
454601                        30.0        QDB.csv       4431  
454602                        14.0        QDB.csv       4431  
454603                         NaN        QDB.csv       1594  

[454604 rows x 11 columns]

In [23]:
df_bi_preco = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\BOTICARIO\C11\preço BI\TABELA DE PREÇOS (2).xlsx")

df_bi_preco = df_bi_preco.drop(columns=['Descrição','Tipo Preço','CATEGORIA','LINHA','MARCA'])



c:\Users\joao.herculano\AppData\Local\Programs\Python\Python313\Lib\site-packages\openpyxl\styles\stylesheet.py:237: UserWarning: Workbook contains no default style, apply openpyxl's default
  warn("Workbook contains no default style, apply openpyxl's default")


In [24]:
df_final = pd.merge(left=df_tabela,right=df_pdv,on='MATCH',how='left')

df_final = df_final.drop_duplicates()

df_final.shape

(25232, 31)

In [25]:
df_final['PDV'] = df_final['PDV'].astype('Int64')
df_final['Código'] = df_final['Código'].astype('Int64')


df_final = pd.merge(left=df_final,right=df_draft,left_on=['PDV','Código'],right_on=['PDV','SKU'],how='left')
df_final.shape

(25232, 62)

In [26]:
df_final[(df_final['Código'] == 52023) & (df_final['PDV'] == 23712)]['Histórico de Vendas do Ciclo 202505']

Series([], Name: Histórico de Vendas do Ciclo 202505, dtype: float64)

In [27]:
df_final = df_final.drop(columns=['Sortimento P', 'Sortimento M',
       'Sortimento G','MARCA','SKU'])

In [28]:
calendario = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\CICLO 9\CALENDARIO_CICLO\Ciclo_Expandido_com_Datas.xlsx")


In [29]:
#ignorando a PDV que ainda não está online
df_pdv = df_pdv[df_pdv['DESCRIÇÃO PDV'] != '23813-COMERCIO-HIB VALENTE']

**ALTERAR NOME DA COLUNA "ARQUIVO_ORIGEM" PARA UMA DAS OPÇÕES ABAIXO:**

*BOT.csv* 

*EUD.csv*

*QDB.csv*

In [30]:
calendario['Date'] = pd.to_datetime(calendario['Date'])

# Get today (normalized to midnight)
today = pd.Timestamp("today").normalize()

calendario['NUM_CICLO'] = calendario['Ciclo'].str[-2:].astype(int)
calendario['ANO_CICLO'] = calendario['Ciclo'].str[0:5]


calendario = calendario[calendario['MARCA'] == "BOTICARIO"]

calendario = calendario.drop(columns='MARCA')

calendario['CICLOMAIS2'] = calendario['ANO_CICLO'].astype(str) + (calendario['NUM_CICLO'].astype(int) + 2).astype(str).str.zfill(2) # >>>>>>>>> MUDAR PRA CICLO CORRETO 

ciclo_mais2 = calendario[calendario['Date'].dt.normalize() == today]['CICLOMAIS2'].iloc[0]


# Filter rows where date matches today
filtered_calendario = calendario[calendario['Ciclo'] == ciclo_mais2][:1]


filtered_calendario['dias_ate_inicio'] = filtered_calendario['INICIO CICLO'].iloc[0] - today

filtered_calendario['dias_ate_inicio'] = filtered_calendario['dias_ate_inicio'].dt.days.astype(int)

filtered_calendario


Ciclo INICIO CICLO  FIM CICLO  DURAÇÃO       Date  NUM_CICLO  \
2241  C202511   2025-07-21 2025-08-10       21 2025-07-21         11   

     ANO_CICLO CICLOMAIS2  dias_ate_inicio  
2241     C2025    C202513               38

In [31]:
filtered_calendario['MATCH'] = 1

In [32]:
df_pdv['UF'] = np.where(df_pdv['UF'] == 'VDC','BA',df_pdv['UF'])

In [33]:
#df_tabela = df_tabela[(df_tabela['Tipo de promoção'] == "Revendedor" ) | (df_tabela['Tipo de promoção'] == "Promoções") |(df_tabela['Tipo de promoção'] == "Promoções | Revendedor" )]

In [34]:
df_draft['PDV'] = df_draft['PDV'].astype(str)

In [35]:
df_final = pd.merge(left=df_final, right=filtered_calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO','MATCH','dias_ate_inicio']], on='MATCH',how='left')
df_final.shape

(25232, 62)

In [36]:
df_final['Código'] = df_final['Código'].astype('Int64') 
df_final['PDV'] = df_final['PDV'].astype('Int64') 

df_estoque['PDV'] = df_estoque['PDV'].astype('Int64') 
df_estoque['SKU_FINAL'] = df_estoque['SKU_FINAL'].astype('Int64') 

df_final = pd.merge(left=df_final,right=df_estoque,right_on=['PDV','SKU_FINAL'],left_on=['PDV','Código'],how='left')
df_final.shape

(30861, 72)

In [37]:
df_final['Código'] = df_final['Código'].astype('str')

df_bi_preco['SKU2'] = df_bi_preco['SKU2'].astype('str')

df_final = pd.merge(left=df_final,right=df_bi_preco,right_on=['UF','SKU2'],left_on=['UF','Código'],how='left')
df_final.shape   

(30861, 76)

In [38]:
df_bi_preco['SKU1'] = df_bi_preco['SKU1'].astype(str).str.replace('.0','',regex=False) 

df_final = pd.merge(left=df_final,right=df_bi_preco[['SKU1', 'SKU2', 'UF', 'PC', 'PV']],right_on=['UF','SKU1'],left_on=['UF','Código'],how='left')
df_final.shape   

(30950, 80)

In [39]:
df_final['PRECO DE COMPRA'] = np.where(~df_final['PC_x'].isna(),df_final['PC_x'],df_final['PC_y'])

df_final['PRECO DE VENDA'] = np.where(~df_final['PV_x'].isna(),df_final['PV_x'],df_final['PV_y'])



In [40]:
df_final['CANAL'] = np.where((df_final['CANAL'] == 'LJ') | (df_final['CANAL'] == 'HIB'), "TODOS" , np.where((df_final['CANAL'] == 'CD') | (df_final['CANAL'] == 'VD'), "VD", df_final['CANAL']))

df_final['CANAL'].value_counts()

CANAL
TODOS    23509
VD        6445
Name: count, dtype: int64

In [41]:
df_estoque = df_estoque.rename(columns={'SKU_FINAL':'SKU_PARA_VALIDACAO'})

df_estoque['SKU_PARA_VALIDACAO'] = df_estoque['SKU_PARA_VALIDACAO'].astype('Int64')

df_final = pd.merge( left= df_final, right = df_estoque[['SKU_PARA_VALIDACAO','Arquivo_Origem']], left_on= 'SKU', right_on='SKU_PARA_VALIDACAO', how='left')

df_final = df_final.drop_duplicates()

In [42]:
df_final = df_final.drop(columns=['SKU1_x','SKU1_y','SKU2_x','SKU2_y','PC_x', 'PV_x','PC_y', 'PV_y','Subcategoria',
'Carteira Bloqueada Para Novos Pedidos',
'Quantidade por caixa'
])

In [43]:
df_final['UFPRODUTO'] = df_final['UF'].astype(str) + df_final['SKU'].astype(str)


In [44]:
df_final['Projeção Próximo Ciclo + 1'] =df_final['Projeção Próximo Ciclo + 1'] - df_final['Projeção Próximo Ciclo'] # projeção do ciclo em estudo

In [45]:
df_final['Data Prevista Regularização'] = df_final['Data Prevista Regularização'].astype(str).replace('0','REGULAR')

In [46]:
df_final = df_final.rename(columns={'Compra inteligente Próximo Ciclo + 1':'Compra inteligente Próximo Ciclo','Arquivo_Origem': 'MARCA'})

In [47]:
df_final = df_final[~df_final['Marca'].isna()]
df_final['Marca'].isna().sum()

np.int64(0)

In [48]:
df_final = df_final.drop_duplicates()
df_final.shape

(30950, 74)

In [49]:
df_final[df_final.columns[26:43]] = df_final[df_final.columns[26:43]].fillna(0)


In [50]:
df_final.columns[26:44]

Index(['Histórico de Vendas do Ciclo 202409',
       'Histórico de Vendas do Ciclo 202410',
       'Histórico de Vendas do Ciclo 202411',
       'Histórico de Vendas do Ciclo 202412',
       'Histórico de Vendas do Ciclo 202413',
       'Histórico de Vendas do Ciclo 202414',
       'Histórico de Vendas do Ciclo 202415',
       'Histórico de Vendas do Ciclo 202416',
       'Histórico de Vendas do Ciclo 202417',
       'Histórico de Vendas do Ciclo 202501',
       'Histórico de Vendas do Ciclo 202502',
       'Histórico de Vendas do Ciclo 202503',
       'Histórico de Vendas do Ciclo 202504',
       'Histórico de Vendas do Ciclo 202505',
       'Histórico de Vendas do Ciclo 202506',
       'Histórico de Vendas do Ciclo 202507',
       'Histórico de Vendas do Ciclo 202508',
       'Histórico de Vendas do Ciclo Atual'],
      dtype='object')

In [51]:
# Define list of target columns
sales_2024_cols = df_final.columns[26:44]
# Create a new column with the row-wise max
df_final['PICO DE VENDAS 2024'] = df_final[sales_2024_cols].max(axis=1)



In [52]:
df_final.columns[37:44]

Index(['Histórico de Vendas do Ciclo 202503',
       'Histórico de Vendas do Ciclo 202504',
       'Histórico de Vendas do Ciclo 202505',
       'Histórico de Vendas do Ciclo 202506',
       'Histórico de Vendas do Ciclo 202507',
       'Histórico de Vendas do Ciclo 202508',
       'Histórico de Vendas do Ciclo Atual'],
      dtype='object')

In [53]:
vendas_6_meses = df_final.columns[37:44]

df_final['Pico Vendas Ultimos 6 ciclos'] = df_final[vendas_6_meses].max(axis=1)

In [54]:
df_final.columns[37:44]

Index(['Histórico de Vendas do Ciclo 202503',
       'Histórico de Vendas do Ciclo 202504',
       'Histórico de Vendas do Ciclo 202505',
       'Histórico de Vendas do Ciclo 202506',
       'Histórico de Vendas do Ciclo 202507',
       'Histórico de Vendas do Ciclo 202508',
       'Histórico de Vendas do Ciclo Atual'],
      dtype='object')

In [55]:
# Define as colunas mensais
colunas_mensais = df_final.columns[26:43]

# Agrupa por PDV e calcula crescimento médio por PDV
def calcular_crescimento(grupo):
    soma_mensal = grupo[colunas_mensais].sum()             # soma por mês
    variacao_mensal = soma_mensal.pct_change().dropna()    # variação percentual mês a mês
    variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

    if len(variacao_mensal) == 0:
        return pd.Series({'CRESCIMENTO': np.nan})

    media = variacao_mensal.mean()
    desvio = variacao_mensal.std()

    limite_sup = media + 2 * desvio
    limite_inf = media - 2 * desvio

    variacoes_filtradas = variacao_mensal[variacao_mensal.between(limite_inf, limite_sup)]
    crescimento = round(variacoes_filtradas.mean(), 4)
    return pd.Series({'CRESCIMENTO': crescimento})

# Aplica a função por PDV
crescimento_por_pdv = df_final.groupby('PDV').apply(calcular_crescimento)

# Merge do resultado de volta no dataframe original
df_final = df_final.merge(crescimento_por_pdv, on='PDV', how='left')


C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_17756\2592201544.py:24: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  crescimento_por_pdv = df_final.groupby('PDV').apply(calcular_crescimento)


In [56]:
# Suponha que os meses estão nas colunas 10 a 26 (17 colunas = 17 meses)
colunas_mensais = df_final.columns[26:43]

# Passo 1: Soma todas as linhas (itens) por mês → resultado: total por mês
soma_mensal = df_final[colunas_mensais].sum()

# Passo 2: Calcula a variação percentual de um mês para o outro
variacao_mensal = soma_mensal.pct_change()
variacao_mensal = variacao_mensal.dropna()

variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

# Passo 3: Calcula a média da variação (ignorando o primeiro NaN)
media_variacao = variacao_mensal[1:].mean()

# Calcula média e desvio padrão
media = variacao_mensal.mean()
desvio = variacao_mensal.std()

# Define limite (ex: 2 desvios padrão)
limite_superior = media + 2 * desvio
limite_inferior = media - 2 * desvio

# Filtra dados dentro do limite
filtro = variacao_mensal.between(limite_inferior, limite_superior)
df_filtrado = variacao_mensal[filtro]
CRESCIMENTO = round(df_filtrado.mean(),4)

df_final['CRESCIMENTO_GERAL'] = CRESCIMENTO

CRESCIMENTO


np.float64(0.0564)

In [57]:
vendas_todos_historicos = df_final.columns[26:44]

df_final['MEDIANA DO HISTÓRICO'] = df_final[vendas_todos_historicos].median(axis=1)

df_final['MEDIA DO HISTÓRICO'] = df_final[vendas_todos_historicos].mean(axis=1)

medi = df_final.groupby(['CANAL'])['MEDIANA DO HISTÓRICO'].max().reset_index()
medi = medi.rename(columns={'MEDIANA DO HISTÓRICO':'med_por_canal'})

df_final = pd.merge(left=df_final, right=medi,on='CANAL',how='left')

medi

CANAL  med_por_canal
0  TODOS           90.5
1     VD          715.0

In [58]:
df_final.columns[28:29].str.split(" ")[0][-1]

'202411'

In [59]:
mesmo_ciclo_ano_passado = df_final.columns[28:29]
ciclo_ano_passado = df_final.columns[28:29].str.split(" ")[0][-1]
df_final[ciclo_ano_passado] = df_final[mesmo_ciclo_ano_passado]

In [60]:
df_final['CRESCIMENTO_FINAL'] = df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO'] #crescimento do pdv

df_final['CRESCIMENTO_FINAL'] = np.where(df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO']>0.8,0.8,df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO'])

df_final['CRESCIMENTO_FINAL'] = np.where(df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO']<0,0,df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO'])

df_final['MEDIANA DO HISTÓRICO'] = np.where(df_final['MEDIANA DO HISTÓRICO']==0,df_final['MEDIA DO HISTÓRICO'] ,df_final['MEDIANA DO HISTÓRICO'])

# Primeiro cálculo intermediário
df_final['PV GINSENG'] = np.where(df_final['CRESCIMENTO_FINAL'] * df_final[ciclo_ano_passado] + df_final[ciclo_ano_passado] <1,
                                    round(df_final['CRESCIMENTO_FINAL'] * df_final['MEDIANA DO HISTÓRICO']+ df_final['MEDIANA DO HISTÓRICO'],0), 
                                    round(df_final['CRESCIMENTO_FINAL']*df_final[ciclo_ano_passado]+df_final[ciclo_ano_passado],0))


df_final.shape

(30950, 84)

In [61]:
df_final.columns[26:39]

Index(['Histórico de Vendas do Ciclo 202409',
       'Histórico de Vendas do Ciclo 202410',
       'Histórico de Vendas do Ciclo 202411',
       'Histórico de Vendas do Ciclo 202412',
       'Histórico de Vendas do Ciclo 202413',
       'Histórico de Vendas do Ciclo 202414',
       'Histórico de Vendas do Ciclo 202415',
       'Histórico de Vendas do Ciclo 202416',
       'Histórico de Vendas do Ciclo 202417',
       'Histórico de Vendas do Ciclo 202501',
       'Histórico de Vendas do Ciclo 202502',
       'Histórico de Vendas do Ciclo 202503',
       'Histórico de Vendas do Ciclo 202504'],
      dtype='object')

In [62]:
df_final = df_final.rename(columns={df_final.columns[39]: "C-4", df_final.columns[40]: "C-3",df_final.columns[41]: "C-2",df_final.columns[42]: "C-1"})

In [63]:
df_final.drop(columns=df_final.columns[26:39], inplace=True)


In [64]:
# List all columns except the two
cols_to_group_by = df_final.columns.difference(['DDV PREVISTO', 'COBERTURA ATUAL'])

# Group and aggregate
df_final_dedup = (
    df_final
    .groupby(list(cols_to_group_by), dropna=False)[['DDV PREVISTO', 'COBERTURA ATUAL']]
    .max()
    .reset_index()
)


In [65]:
df_final_dedup['DDV PREVISTO'] = df_final_dedup['DDV PREVISTO'].fillna(0.01)


In [66]:
df_final_dedup[(df_final['PDV'] == 23712)]['C-3']

76          9.0
152         0.0
228         0.0
304         0.0
380         0.0
          ...  
30610      18.0
30708     129.0
30785     744.0
30861    1074.0
30937     113.0
Name: C-3, Length: 371, dtype: float64

In [67]:
df_final_dedup['DDV PREVISTO'] = np.where(
    df_final_dedup['DDV PREVISTO'] == 0,
    0.01,
    df_final_dedup['DDV PREVISTO']
)


In [68]:
df_final_dedup.columns

Index(['202411', 'ANALISTA', 'Arquivo_Origem_x', 'Arquivo_Origem_y',
       'Ação consumidor', 'Ação revendedor', 'C-1', 'C-2', 'C-3', 'C-4',
       'CANAL', 'COBERTURA ATUAL + TRANSITO', 'CRESCIMENTO',
       'CRESCIMENTO_FINAL', 'CRESCIMENTO_GERAL', 'Canal', 'Categoria',
       'Catálogo', 'Ciclo_x', 'Ciclo_y', 'Classe', 'Código', 'DESCRIÇÃO PDV',
       'DURAÇÃO', 'Data Prevista Regularização', 'Descrição', 'Dias sem venda',
       'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'Estoque Atual',
       'Estoque em Transito', 'FIM CICLO', 'Foco',
       'Histórico de Vendas do Ciclo 202408',
       'Histórico de Vendas do Ciclo Atual', 'IAF', 'INICIO CICLO',
       'Item Desativado', 'MATCH', 'MEDIA DO HISTÓRICO',
       'MEDIANA DO HISTÓRICO', 'Marca', 'PDV', 'PEDIDO PENDENTE',
       'PICO DE VENDAS 2024', 'PRECO DE COMPRA', 'PRECO DE VENDA',
       'PV GINSENG', 'Pedido Pendente', 'Percentual de desconto consumidor',
       'Percentual de desconto revendedor', 'Pico Vendas Ultimos 6 ciclo

In [69]:
df_final_dedup['EST PROJE FINAL CICLO ATUAL'] = (df_final_dedup['Estoque Atual'] + df_final_dedup['Estoque em Transito']) - round(df_final_dedup['dias_ate_inicio'] * df_final_dedup['DDV PREVISTO'],0)

In [70]:
df_final_dedup['EST PROJE FINAL CICLO ATUAL'] = np.where(df_final_dedup['EST PROJE FINAL CICLO ATUAL']<0,0,df_final_dedup['EST PROJE FINAL CICLO ATUAL'])

In [71]:
df_final_dedup['VENDAS R$ PV GINSENG'] = df_final_dedup['PRECO DE VENDA'] * df_final_dedup['PV GINSENG']

In [72]:
df_estoque.columns

Index(['SKU', 'SKU_PARA', 'PDV', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'DDV PREVISTO', 'COBERTURA ATUAL',
       'COBERTURA ATUAL + TRANSITO', 'Arquivo_Origem', 'SKU_PARA_VALIDACAO'],
      dtype='object')

In [73]:
# Columns to bring up front
priority_cols = [
    'SKU',	'Marca',	'INICIO CICLO',
    'FIM CICLO',	'DURAÇÃO',	'PRECO DE COMPRA',	'PRECO DE VENDA',
    'UFPRODUTO',	'Item Desativado',	'Data Prevista Regularização',
    'ANALISTA',	'UF',	'CANAL',	'PDV',	'DESCRIÇÃO PDV',	'Classe',
    'Descrição',	'Categoria',
	'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',	'COBERTURA ATUAL',
    'Pedido Pendente',	'PICO DE VENDAS 2024','Pico Vendas Ultimos 6 ciclos',
    'C-4',	'C-3',	'C-2',	'C-1',	'Histórico de Vendas do Ciclo Atual',
    'Dias sem venda'
]

# All remaining columns
other_cols = [col for col in df_final_dedup.columns if col not in priority_cols]

# Reorder
'Ação consumidor', 'Percentual de desconto consumidor', 'Ação revendedor', 'Percentual de desconto revendedor', '202408'


('Ação consumidor',
 'Percentual de desconto consumidor',
 'Ação revendedor',
 'Percentual de desconto revendedor',
 '202408')

In [74]:
#df_final_dedup = df_final_dedup[priority_cols + other_cols]


In [75]:
df_final_dedup['RBV 202406'] = df_final_dedup['PRECO DE VENDA'] * df_final_dedup[ciclo_ano_passado] 

In [76]:
df_final_dedup['COB PROJETADA'] = np.where(
    df_final_dedup['DDV PREVISTO'] != 0,
    (df_final_dedup['EST PROJE FINAL CICLO ATUAL'] + df_final_dedup['PV GINSENG']) / df_final_dedup['DDV PREVISTO'],
    999)


In [77]:
df_final_dedup.drop(df_final_dedup.columns[39:40], axis=1, inplace=True)


In [78]:
df_final_dedup.drop(columns=['dias_ate_inicio','SKU_FINAL',
                             'CRESCIMENTO'],inplace=True)

In [79]:
#df_final_dedup['MARCA'] = df_final_dedup['MARCA'].str.replace('.csv','',regex=False)

In [80]:
df_final_dedup['COB PROJETADA'] = df_final_dedup['COB PROJETADA'].fillna(999)

In [81]:
marca_promo =  df_estoque['Arquivo_Origem'].iloc[0].replace('.csv','')
marca_promo

'BOT'

In [82]:
df_final_dedup['INICIO CICLO'] = pd.to_datetime(df_final_dedup['INICIO CICLO'], dayfirst=True).dt.strftime('%d/%m/%Y')

df_final_dedup['FIM CICLO'] = pd.to_datetime(df_final_dedup['FIM CICLO'], dayfirst=True).dt.strftime('%d/%m/%Y')

In [83]:
df_final_dedup['Percentual de desconto revendedor'] = np.where((df_final_dedup['Percentual de desconto revendedor'].isna()) & (~df_final_dedup['Percentual de desconto consumidor'].isna()),df_final_dedup['Percentual de desconto consumidor'],df_final_dedup['Percentual de desconto revendedor'])

In [84]:
df_pdv_origi['PDV'] = df_pdv_origi['PDV'].astype('Int64')
df_final_dedup['PDV'] = df_final_dedup['PDV'].astype('Int64')


df_final_dedup = pd.merge(left=df_final_dedup,right=df_pdv_origi[['PDV','CANAL','UF']],how='left',on='PDV')

In [85]:
df_final_dedup['Código'].isna().sum()

np.int64(0)

In [86]:
df_final_dedup.to_excel(r'C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\BOTICARIO\C11\teste.xlsx')

In [87]:
df_final_dedup = df_final_dedup[df_final_dedup['Código']!= '<NA>']


In [88]:
df_vdc = pd.read_csv(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\BOTICARIO\C10\VENDA VITORIA 2024\VENDA VITORIA.csv")

df_vdc['PRODUTO'] = df_vdc['PRODUTO'].astype('Int64')

df_final_dedup['Código'] = df_final_dedup['Código'].astype('Int64')

df_final_dedup =pd.merge(left=df_final_dedup,right=df_vdc[['PDV GINSENG','PRODUTO',ciclo_ano_passado]],left_on= ['PDV','Código'],right_on= ['PDV GINSENG','PRODUTO'],how='left' )

df_final_dedup[df_final_dedup.columns[-1]] = df_final_dedup[df_final_dedup.columns[-1]].fillna(0)

In [89]:
df_final_dedup.head()

202411_x ANALISTA Arquivo_Origem_x Arquivo_Origem_y  \
0       0.0   DANIEL          BOT.csv          BOT.csv   
1       0.0   DANIEL          BOT.csv          BOT.csv   
2       0.0   DANIEL          BOT.csv          BOT.csv   
3       0.0   DANIEL          BOT.csv          BOT.csv   
4       0.0   DANIEL          BOT.csv          BOT.csv   

                                 Ação consumidor  \
0  BODY SPRAY BOTICOLLECTION COM 20% DE DESCONTO   
1  BODY SPRAY BOTICOLLECTION COM 20% DE DESCONTO   
2  BODY SPRAY BOTICOLLECTION COM 20% DE DESCONTO   
3  BODY SPRAY BOTICOLLECTION COM 20% DE DESCONTO   
4  BODY SPRAY BOTICOLLECTION COM 20% DE DESCONTO   

                                 Ação revendedor  C-1  C-2  C-3  C-4  ...  \
0  BODY SPRAY BOTICOLLECTION COM 20% DE DESCONTO  0.0  0.0  0.0  1.0  ...   
1  BODY SPRAY BOTICOLLECTION COM 20% DE DESCONTO  0.0  2.0  0.0  0.0  ...   
2  BODY SPRAY BOTICOLLECTION COM 20% DE DESCONTO  2.0  0.0  0.0  1.0  ...   
3  BODY SPRAY BOTICOLLECTION COM 20% DE DESCONTO  3.0  0.0  0.0  3.0  ...   
4  BODY SPRAY BOTICOLLECTION COM 20% DE DESCONTO  4.0  0.0  0.0  0.0  ...   

  COBERTURA ATUAL  EST PROJE FINAL CICLO ATUAL  VENDAS R$ PV GINSENG  \
0           166.0                          4.0                   NaN   
1            45.0                          1.0                   NaN   
2           200.0                          2.0                   NaN   
3             0.0                          3.0                   NaN   
4           100.0                          1.0                   NaN   

   RBV 202406 COB PROJETADA CANAL_y UF_y  PDV GINSENG PRODUTO 202411_y  
0         NaN    166.666667      LJ   BA          NaN    <NA>      0.0  
1         NaN    100.000000      LJ  VDC          NaN    <NA>      0.0  
2         NaN    200.000000      LJ   BA          NaN    <NA>      0.0  
3         NaN     83.333333      LJ   BA          NaN    <NA>      0.0  
4         NaN    100.000000      VD  VDC      23703.0   29046      0.0  

[5 rows x 76 columns]

In [90]:
df_final_dedup.columns[-1]

'202411_y'

In [91]:
df_final_dedup[df_final_dedup.columns[0]] = np.where(df_final_dedup[df_final_dedup.columns[-1]]>0,df_final_dedup[df_final_dedup.columns[-1]],df_final_dedup[df_final_dedup.columns[0]])

In [92]:
df_final_dedup = df_final_dedup.drop(columns=['Arquivo_Origem_x','Arquivo_Origem_y','CANAL_x','Canal',
                                              'Ciclo_x','Ciclo_y','DURAÇÃO','FIM CICLO','Foco','INICIO CICLO','MATCH',
                                              'PRECO DE COMPRA','SKU','SKU_PARA','SKU_PARA_VALIDACAO',
                                              'Tipo de pedido',	'Tipo de produto','UFPRODUTO','Unidade de negócio','EST PROJE FINAL CICLO ATUAL',
                                              'UF_x','RBV 202406','Região','Catálogo','SKU','VENDAS R$ PV GINSENG','Data Prevista Regularização',
                                              'IAF', 'Item Desativado','Tipo de promoção','PDV GINSENG','PRODUTO','202411_y',
                                              'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO','COBERTURA ATUAL + TRANSITO',
                                              'DDV PREVISTO',	'COB PROJETADA','COBERTURA ATUAL',
                                              'CRESCIMENTO_FINAL',	'CRESCIMENTO_GERAL','med_por_canal','PEDIDO PENDENTE'])

In [93]:
df_final_dedup = df_final_dedup.rename(columns={'CANAL_y':'CANAL','UF_y':'UF','Marca':'LINHA','202410_x':'202410'})


In [94]:
df_final_dedup.columns

Index(['202411_x', 'ANALISTA', 'Ação consumidor', 'Ação revendedor', 'C-1',
       'C-2', 'C-3', 'C-4', 'Categoria', 'Classe', 'Código', 'DESCRIÇÃO PDV',
       'Descrição', 'Dias sem venda', 'Estoque Atual', 'Estoque em Transito',
       'Histórico de Vendas do Ciclo 202408',
       'Histórico de Vendas do Ciclo Atual', 'MEDIANA DO HISTÓRICO', 'LINHA',
       'PDV', 'PICO DE VENDAS 2024', 'PRECO DE VENDA', 'PV GINSENG',
       'Pedido Pendente', 'Percentual de desconto consumidor',
       'Percentual de desconto revendedor', 'Pico Vendas Ultimos 6 ciclos',
       'Projeção Próximo Ciclo', 'Projeção Próximo Ciclo + 1',
       'Promoção Próximo Ciclo + 1', 'SUPERVISOR', 'CANAL', 'UF'],
      dtype='object')

In [95]:
df_final_dedup[(df_final['PDV'] == 23712)]['C-3']

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_17756\4017566689.py:1: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  df_final_dedup[(df_final['PDV'] == 23712)]['C-3']


76         9.0
152        0.0
228        0.0
304        0.0
380        0.0
         ...  
29314      6.0
29390     26.0
29466    137.0
29542    116.0
29618     23.0
Name: C-3, Length: 355, dtype: float64

In [96]:
priority_cols = ['SUPERVISOR','ANALISTA','UF','CANAL','LINHA','PDV','DESCRIÇÃO PDV','Código','Descrição','Categoria', 
'Classe','Percentual de desconto consumidor','Ação consumidor','Percentual de desconto revendedor','Ação revendedor','C-1',
'C-2', 'C-3', 'C-4','Histórico de Vendas do Ciclo Atual','Estoque Atual','Estoque em Transito','Pedido Pendente',
'Projeção Próximo Ciclo + 1','Projeção Próximo Ciclo']

# All remaining columns
other_cols = [col for col in df_final_dedup.columns if col not in priority_cols]

# Reorder
df_final_dedup = df_final_dedup[priority_cols + other_cols]

df_final_dedup['SUGESTÃO ABASTECIMENTO'] = ''


In [97]:
df_final_dedup = df_final_dedup.drop_duplicates()

In [98]:
df_final_dedup['PV GINSENG'].sum()

np.float64(75876.0)

In [99]:
df_final_dedup[df_final_dedup['PDV'] == 23712]['PICO DE VENDAS 2024'].isna().sum()

np.int64(0)

In [100]:
# Export to Excel
output_file = f'C:\\Users\\joao.herculano\\Documents\\promoção_{marca_promo}_{ciclo_mais2}.{hoje}.xlsx'
with pd.ExcelWriter(output_file, engine='openpyxl') as writer:
    df_final_dedup.to_excel(writer, index=False)

# Apply styles
wb = load_workbook(output_file)
ws = wb['Sheet1']

# Style header
header_fill = PatternFill(start_color='ADD8E6', end_color='ADD8E6', fill_type='solid')  # Light Blue
header_font = Font(color='FFFFFF', bold=True)  # White & Bold

for cell in ws[1]:
    cell.fill = header_fill
    cell.font = header_font

# Style rows: gray/white alternating
gray_fill = PatternFill(start_color='DDDDDD', end_color='DDDDDD', fill_type='solid')  # Light gray

for i, row in enumerate(ws.iter_rows(min_row=2, max_row=ws.max_row), start=2):
    if i % 2 == 0:
        for cell in row:
            cell.fill = gray_fill

# Save styled workbook
wb.save(output_file)


coisas q saem

Lançamento
Subcategoria
Projeção Próximo Ciclo 
Promoção Próximo Ciclo
Compra inteligente semanal/Sugestão de compra
Compra inteligente Próximo Ciclo
Planograma
Carteira Bloqueada Para Novos Pedidos
Quantidade por caixa
Preço Sell In
Quantidade
Item analisado
Tipo Preço

>>>>>>>>>>>>>NAO ESTÁ PEGANDO O MERGE COM O DF_ESTOQUE


CRIAR PROJEÇÃO DE VENDA DO CICLO ATUAL
Compra inteligente Próximo Ciclo + 1 >>>>>>> RENAME PRA NOROMAL